# Tabular Data Analysis and Preliminar Classification

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt
import scipy.stats as sp
from joblib import dump, load
from collections import namedtuple

%matplotlib inline
plt.style.use('seaborn')
pd.set_option('display.max_columns', 150)
pd.set_option('display.max_rows', 150)


from google.colab import drive
import os

drive.mount('/content/gdrive', force_remount=True)
os.chdir('/content/gdrive/MyDrive/Lucas_Thimoteo/mmml-alzheimer-diagnosis')

In [ ]:
!rm -r /content/gdrive/MyDrive/Lucas_Thimoteo/mmml-alzheimer-diagnosis/src.egg-info
!python3 -m pip install -e /content/gdrive/MyDrive/Lucas_Thimoteo/mmml-alzheimer-diagnosis/.

Obtaining file:///content/gdrive/MyDrive/Lucas_Thimoteo/mmml-alzheimer-diagnosis
  Found existing installation: src 0.1.0
    Can't uninstall 'src'. No files were found to uninstall.
  Running setup.py develop for src


In [ ]:
!pip install pycaret

     |████████████████████████████████| 266kB 5.3MB/s 
     |████████████████████████████████| 256kB 16.0MB/s 
     |████████████████████████████████| 81kB 6.0MB/s 
     |████████████████████████████████| 6.8MB 14.4MB/s 
     |████████████████████████████████| 61kB 6.8MB/s 
     |████████████████████████████████| 174kB 44.7MB/s 
     |████████████████████████████████| 1.7MB 44.8MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 14.2MB 40.7MB/s 
     |████████████████████████████████| 276kB 39.3MB/s 
     |████████████████████████████████| 2.0MB 36.9MB/s 
     |████████████████████████████████| 112kB 56.7MB/s 
     |████████████████████████████████| 1.4MB 14.0MB/s 
     |████████████████████████████████| 3.1MB 32.4MB/s 
     |████████████████████████████████| 112kB 48.6MB/s 
     |████████████████████████████████| 61kB 6.9MB/

In [ ]:
pip install interpret

     |████████████████████████████████| 5.8MB 4.2MB/s 
     |████████████████████████████████| 1.8MB 37.5MB/s 
     |████████████████████████████████| 81kB 8.1MB/s 
     |████████████████████████████████| 3.6MB 42.5MB/s 
     |████████████████████████████████| 5.6MB 32.3MB/s 
     |████████████████████████████████| 296kB 36.5MB/s 
     |████████████████████████████████| 276kB 41.3MB/s 
     |████████████████████████████████| 788kB 35.7MB/s 
     |████████████████████████████████| 122kB 45.5MB/s 
     |████████████████████████████████| 860kB 34.1MB/s 
     |████████████████████████████████| 358kB 36.7MB/s 
     |████████████████████████████████| 1.0MB 33.6MB/s 
     |████████████████████████████████| 3.5MB 32.8MB/s 
     |████████████████████████████████| 92kB 9.5MB/s 
     |████████████████████████████████| 256kB 51.3MB/s 
     |████████████████████████████████| 368kB 35.2MB/s 
     |████████████████████████████████| 358kB 37.0MB/s 
  Created wheel for dash-table: filename=dash_table-4

# Data Preprocessing with ADNIMERGE file

ADNIMERGE contains the key clinical features for the ADNI database

In [ ]:
df_adni_merge_dict = pd.read_csv('./data/tabular/ADNIMERGE_DICT.csv',low_memory=False)
# df_data_dict = pd.read_csv('./data/tabular/DATADIC.csv',low_memory=False)
# df_adni_merge_dict.to_excel('./data/tabular/ADNIMERGE_DICT.xlsx',index=False)

df_adni_merge = pd.read_csv('./data/tabular/ADNIMERGE.csv',low_memory=False)
baseline_cols = [x for x in df_adni_merge.columns if '_bl' in x and 'DX' not in x] + ['update_stamp']
df_adni_merge.drop(baseline_cols,axis=1,inplace=True)

df_adni_merge.loc[df_adni_merge['DX'] == 'Dementia','DX'] = 'AD'

In [ ]:
df_adni_merge['DX_bl'].value_counts()

LMCI    5078
CN      4587
EMCI    2797
AD      1688
SMC     1109
Name: DX_bl, dtype: int64

In [ ]:
df_adni_merge.value_counts(subset=['DX_bl','DX'])

DX_bl  DX 
LMCI   MCI    2657
CN     CN     2645
EMCI   MCI    1732
AD     AD     1192
LMCI   AD      968
SMC    CN      732
CN     MCI     257
EMCI   CN      150
LMCI   CN      139
EMCI   AD      107
CN     AD       79
SMC    MCI      48
AD     MCI      11
SMC    AD        3
dtype: int64

In [ ]:
df_adni_merge.loc[df_adni_merge['DX_bl'] == 'LMCI','DX_bl'] = 'MCI'
df_adni_merge.loc[df_adni_merge['DX_bl'] == 'EMCI','DX_bl'] = 'MCI'
df_adni_merge.loc[df_adni_merge['DX_bl'] == 'SMC','DX_bl'] = 'CN'

In [ ]:
df_adni_merge['DX_bl'].value_counts()

MCI    7875
CN     5696
AD     1688
Name: DX_bl, dtype: int64

In [ ]:
df_adni_merge_dict[['FLDNAME','TEXT']]

FLDNAME                                               TEXT
0                RID                              Participant roster ID
1               PTID                            Original study protocol
2              ABETA                                          CSF ABETA
3            VISCODE                                         Visit code
4               SITE                                               Site
..               ...                                                ...
108      TRABSCOR_bl                                           Trails B
109    mPACCdigit_bl  ADNI modified Preclinical Alzheimer's Cognitiv...
110  mPACCtrailsB_bl  ADNI modified Preclinical Alzheimer's Cognitiv...
111     FLDSTRENG_bl                                 MRI Field Strength
112     FSVERSION_bl                        FreeSurfer Software Version

[113 rows x 2 columns]

In [ ]:
neuropsychological_cols = ['CDRSB','ADAS11', 'ADAS13', 'ADASQ4', 'MMSE', 'RAVLT_immediate',
'RAVLT_learning', 'RAVLT_forgetting', 'RAVLT_perc_forgetting',
'LDELTOTAL', 'DIGITSCOR', 'TRABSCOR', 'FAQ', 'MOCA', 'EcogPtMem',
'EcogPtLang', 'EcogPtVisspat', 'EcogPtPlan', 'EcogPtOrgan',
'EcogPtDivatt', 'EcogPtTotal', 'EcogSPMem', 'EcogSPLang',
'EcogSPVisspat', 'EcogSPPlan', 'EcogSPOrgan', 'EcogSPDivatt','EcogSPTotal']

demographics_cols = ['AGE','PTGENDER', 'PTEDUCAT','PTETHCAT', 'PTRACCAT', 'PTMARRY']

id_cols = ['RID', 'PTID', 'VISCODE', 'SITE', 'COLPROT', 'ORIGPROT', 'EXAMDATE','IMAGEUID','DX','DX_bl']

In [ ]:
df_adni_merge = df_adni_merge[id_cols + demographics_cols + neuropsychological_cols]

In [ ]:
df_adni_merge.shape

(15278, 44)

In [ ]:
df_adni_merge['DX'].value_counts()

MCI    4705
CN     3666
AD     2349
Name: DX, dtype: int64

In [ ]:
print("Amount of null data in columns:")
df_adni_merge.isnull().sum()

Amount of null data in columns:


RID                          0
PTID                         0
VISCODE                      0
SITE                         0
COLPROT                      0
ORIGPROT                     0
EXAMDATE                     0
IMAGEUID                  7060
DX                        4558
DX_bl                       19
AGE                          7
PTGENDER                     0
PTEDUCAT                     0
PTETHCAT                     0
PTRACCAT                     0
PTMARRY                      0
CDRSB                     4335
ADAS11                    4562
ADAS13                    4659
ADASQ4                    4535
MMSE                      4521
RAVLT_immediate           4645
RAVLT_learning            4644
RAVLT_forgetting          4675
RAVLT_perc_forgetting     4748
LDELTOTAL                 6552
DIGITSCOR                11478
TRABSCOR                  4968
FAQ                       4328
MOCA                      8543
EcogPtMem                 8308
EcogPtLang                8325
EcogPtVi

In [ ]:
df_adni_merge = df_adni_merge[~df_adni_merge['DX'].isnull()]

df_adni_merge.rename(inplace=True,
    columns={
    'PTRACCAT':'RACE',
    'PTMARRY':'MARRIED',
    'PTEDUCAT':'YEARS_EDUCATION',
    'PTGENDER':'MALE',
    'PTETHCAT':'HISPANIC',
    'DX':'DIAGNOSIS',
    'DX_bl':'DIAGNOSIS_BASELINE',
    'PTID':'SUBJECT'
})

df_adni_merge.loc[df_adni_merge['RACE'].isin(["More than one",'Unkown','Unknown','Hawaiian/Other PI','Am Indian/Alaskan']),'RACE'] = 'Other races'
df_adni_merge['RACE_WHITE'] = (df_adni_merge['RACE'] == 'White').astype(int)
df_adni_merge['RACE_BLACK'] = (df_adni_merge['RACE'] == 'Black').astype(int)
df_adni_merge['RACE_ASIAN'] = (df_adni_merge['RACE'] == 'Asian').astype(int)
# df_adni_merge['RACE_OTHER'] = df_adni_merge['RACE'] == 'Other races'

df_adni_merge.loc[df_adni_merge['HISPANIC'] == 'Not Hisp/Latino','HISPANIC'] = 0
df_adni_merge.loc[df_adni_merge['HISPANIC'] == 'Unknown','HISPANIC'] = 0
df_adni_merge.loc[df_adni_merge['HISPANIC'] == 'Hisp/Latino','HISPANIC'] = 1

df_adni_merge['IMAGEUID'] = df_adni_merge['IMAGEUID'].fillna(999999)
df_adni_merge['IMAGEUID'] = df_adni_merge['IMAGEUID'].astype(int)

df_adni_merge.loc[df_adni_merge['DIAGNOSIS'] == 'AD','DIAGNOSIS'] = 1
df_adni_merge.loc[df_adni_merge['DIAGNOSIS'] == 'CN','DIAGNOSIS'] = 0
df_adni_merge.loc[df_adni_merge['DIAGNOSIS'] == 'MCI','DIAGNOSIS'] = 2

df_adni_merge.loc[df_adni_merge['MALE'] == 'Male','MALE'] = 1
df_adni_merge.loc[df_adni_merge['MALE'] == 'Female','MALE'] = 0

df_adni_merge['WIDOWED'] = (df_adni_merge['MARRIED'] == 'Widowed').astype(int)
df_adni_merge['DIVORCED'] = (df_adni_merge['MARRIED'] == 'Divorced').astype(int)
df_adni_merge['NEVER_MARRIED'] = (df_adni_merge['MARRIED'] == 'Never married').astype(int)

df_adni_merge['MARRIED'] = (df_adni_merge['MARRIED'] == 'Married').astype(int)

In [ ]:
df_adni_merge.to_csv("./data/tabular/DERMO_NEURO_PSYCHOLOG_PROCESSED.csv",index=False)

# ML Experimentation - Demographics + Cognitive Tests

## Base Code

In [ ]:
def train_test_split_by_subject(df,test_size = 0.3,labels = ['AD','CN'],label_column = 'MACRO_GROUP'):
    
    '''
    Splits the dataset on train and test, at patient level (to avoid data leakage).
    This process executes a stratified random split, that is, it maintains the proportion of each class in the sets.
    
    Parameters
    ----------

    df: Reference dataframe containing information about patients.
    
    test_size: test dataset size. Value must be between bigger than 0 and less than 1.

    labels: Label of the classes.
    
    label_column: Name of the column in the dataframe that contains the classes.
    
    only_ids: Flag to return only a list with IDs of the patients. If False, it returns the entire reference dataframes.

    Returns
    ----------
    Tuple with train and test reference datasets: df_train, df_test
    
    '''

    train = []
    test = []
    df_classes = df[df[label_column].isin(labels)]

    # split by subject id
    subjects = df_classes['SUBJECT'].unique()
    np.random.shuffle(subjects)
    # df_major_class = df_classes.groupby([''])

    for label in labels:
        subjects = df_classes.query(label_column +" == @label")['SUBJECT'].unique()
        np.random.shuffle(subjects)

        test_subjects_quantity = int(np.ceil(test_size * subjects.shape[0]))
        test_subjects = subjects[:test_subjects_quantity]
        train_subjects = subjects[test_subjects_quantity:]
        
        df_train_cl = df_classes.query("SUBJECT in @train_subjects")
        df_test_cl = df_classes.query("SUBJECT in @test_subjects")
        train.append(df_train_cl)
        test.append(df_test_cl)

    df_train = pd.concat(train).sample(frac=1).reset_index(drop=True)
    df_test = pd.concat(test).sample(frac=1).reset_index(drop=True)

    return df_train,df_test

In [ ]:
!pip install pycaret

In [ ]:
!pip insall interpret

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt
import scipy.stats as sp
from joblib import dump, load
from collections import namedtuple

%matplotlib inline
plt.style.use('seaborn')
pd.set_option('display.max_columns', 150)
pd.set_option('display.max_rows', 150)

from google.colab import drive
import os

drive.mount('/content/gdrive', force_remount=True)
os.chdir('/content/gdrive/MyDrive/Lucas_Thimoteo/mmml-alzheimer-diagnosis')

Mounted at /content/gdrive


In [ ]:
# from src.model_training.mri_train_test_split import train_test_split_by_subject

from interpret.glassbox import ExplainableBoostingClassifier
from pycaret.utils import enable_colab
from pycaret.classification import *
# from pycaret.anomaly import *
from sklearn.metrics import fbeta_score,make_scorer
enable_colab()

Colab mode enabled.


## Final data processing

In [ ]:
df_adni_merge = pd.read_csv("./data/tabular/COGNITIVE_DATA_PROCESSED.csv")

# organized_cols = ['SUBJECT','DIAGNOSIS','DIAGNOSIS_BASELINE','AGE', 'MALE', 'YEARS_EDUCATION', 'HISPANIC',
# 'RACE_WHITE', 'RACE_BLACK', 'RACE_ASIAN',
# 'MARRIED','WIDOWED','DIVORCED','NEVER_MARRIED', 'CDRSB', 'ADAS11', 'ADAS13', 'ADASQ4', 'MMSE',
# 'RAVLT_immediate', 'RAVLT_learning', 'RAVLT_forgetting',
# 'RAVLT_perc_forgetting', 'LDELTOTAL', 'DIGITSCOR', 'TRABSCOR', 'FAQ',
# 'MOCA', 'EcogPtMem', 'EcogPtLang', 'EcogPtVisspat', 'EcogPtPlan',
# 'EcogPtOrgan', 'EcogPtDivatt', 'EcogPtTotal', 'EcogSPMem', 'EcogSPLang',
# 'EcogSPVisspat', 'EcogSPPlan', 'EcogSPOrgan', 'EcogSPDivatt',
# 'EcogSPTotal']

# df_adni_merge = df_adni_merge[organized_cols]

In [ ]:
df_adni_merge['DIAGNOSIS'].value_counts()

2    4705
0    3666
1    2349
Name: DIAGNOSIS, dtype: int64

In [ ]:
# ecog_cols = ['EcogPtMem', 'EcogPtLang', 'EcogPtVisspat', 'EcogPtPlan', 'EcogPtOrgan',
#        'EcogPtDivatt', 'EcogPtTotal', 'EcogSPMem', 'EcogSPLang',
#        'EcogSPVisspat', 'EcogSPPlan', 'EcogSPOrgan', 'EcogSPDivatt',
#        'EcogSPTotal','LDELTOTAL','DIGITSCOR']
# df_adni_merge = df_adni_merge.drop(ecog_cols,axis=1).dropna() 
df_adni_merge = df_adni_merge.dropna() 
df_adni_merge.shape

(6210, 34)

In [ ]:
# df_adni_merge.to_csv("./data/tabular/DERMO_NEURO_PSYCHOLOG_PROCESSED_FINAL.csv",index=False)

In [ ]:
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['AD','MCI','CN'])
print("All classes:")
print('Train samples: ',df_train.shape[0])
print('Train subjects: ',df_train['SUBJECT'].unique().shape[0])
print('')
print('test samples: ',df_test.shape[0])
print('test subjects: ',df_test['SUBJECT'].unique().shape[0])

All classes:
Train samples:  4974
Train subjects:  1338

test samples:  1236
test subjects:  336


In [ ]:

print('-----------------------')
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['AD','CN'])
print("AD vs CN:")
print('Train samples: ',df_train.shape[0])
print('Train subjects: ',df_train['SUBJECT'].unique().shape[0])
print('')
print('test samples: ',df_test.shape[0])
print('test subjects: ',df_test['SUBJECT'].unique().shape[0])

print('-----------------------')
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['AD','MCI'])
print("AD vs MCI:")
print('Train samples: ',df_train.shape[0])
print('Train subjects: ',df_train['SUBJECT'].unique().shape[0])
print('')
print('test samples: ',df_test.shape[0])
print('test subjects: ',df_test['SUBJECT'].unique().shape[0])

print('-----------------------')
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['MCI','CN'])
print("MCI vs CN:")
print('Train samples: ',df_train.shape[0])
print('Train subjects: ',df_train['SUBJECT'].unique().shape[0])
print('')
print('test samples: ',df_test.shape[0])
print('test subjects: ',df_test['SUBJECT'].unique().shape[0])

-----------------------
AD vs CN:
Train samples:  2313
Train subjects:  720

test samples:  608
test subjects:  181
-----------------------
AD vs MCI:
Train samples:  2936
Train subjects:  766

test samples:  764
test subjects:  192
-----------------------
MCI vs CN:
Train samples:  4645
Train subjects:  1190

test samples:  1154
test subjects:  299


## Experiment - CN vs MCI

In [ ]:
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['MCI','CN'])

df_train.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)
df_test.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)

exp_clinical = setup(
data = df_train,
test_data=df_test, 
target = 'DIAGNOSIS', 
transformation=True,remove_multicollinearity = False,
session_id=1,experiment_name = 'adni_tabular_cn_mci',silent=True)

Description                Value
0                               session_id                    1
1                                   Target            DIAGNOSIS
2                              Target Type           Multiclass
3                            Label Encoded     0: 0, 1: 1, 2: 2
4                            Original Data           (4609, 24)
5                           Missing Values                False
6                         Numeric Features                   13
7                     Categorical Features                   10
8                         Ordinal Features                False
9                High Cardinality Features                False
10                 High Cardinality Method                 None
11                   Transformed Train Set           (4609, 37)
12                    Transformed Test Set           (1190, 37)
13                      Shuffle Train-Test                 True
14                     Stratify Train-Test                False
15                          Fold Generator      StratifiedKFold
16                             Fold Number                   10
17                                CPU Jobs                   -1
18                                 Use GPU                False
19                          Log Experiment                False
20                         Experiment Name  adni_tabular_cn_mci
21                                     USI                 042b
22                         Imputation Type               simple
23          Iterative Imputation Iteration                 None
24                         Numeric Imputer                 mean
25      Iterative Imputation Numeric Model                 None
26                     Categorical Imputer             constant
27  Iterative Imputation Categorical Model                 None
28           Unknown Categoricals Handling       least_frequent
29                               Normalize                False
30                        Normalize Method                 None
31                          Transformation                 True
32                   Transformation Method          yeo-johnson
33                                     PCA                False
34                              PCA Method                 None
35                          PCA Components                 None
36                     Ignore Low Variance                False
37                     Combine Rare Levels                False
38                    Rare Level Threshold                 None
39                         Numeric Binning                False
40                         Remove Outliers                False
41                      Outliers Threshold                 None
42                Remove Multicollinearity                False
43             Multicollinearity Threshold                 None
44                              Clustering                False
45                    Clustering Iteration                 None
46                     Polynomial Features                False
47                       Polynomial Degree                 None
48                    Trignometry Features                False
49                    Polynomial Threshold                 None
50                          Group Features                False
51                       Feature Selection                False
52                Feature Selection Method              classic
53            Features Selection Threshold                 None
54                     Feature Interaction                False
55                           Feature Ratio                False
56                   Interaction Threshold                 None
57                           Fix Imbalance                False
58                    Fix Imbalance Method                SMOTE

In [ ]:
# selected_models = ['lr','rbfsvm','rf']
top5 = compare_models(sort='AUC',n_select = 5,turbo=False,cross_validation = True,fold = 5)

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.8972  0.9656  0.8538  0.8984   
lightgbm  Light Gradient Boosting Machine    0.8982  0.9642  0.8694  0.8987   
gbc          Gradient Boosting Classifier    0.8935  0.9616  0.8699  0.8941   
rf               Random Forest Classifier    0.8933  0.9608  0.8596  0.8946   
lr                    Logistic Regression    0.8898  0.9556  0.8608  0.8900   
lda          Linear Discriminant Analysis    0.8663  0.9475  0.8502  0.8699   
knn                K Neighbors Classifier    0.8549  0.9369  0.7910  0.8536   
dt               Decision Tree Classifier    0.8377  0.8566  0.8193  0.8382   
nb                            Naive Bayes    0.6337  0.8386  0.7378  0.7543   
ada                  Ada Boost Classifier    0.7817  0.8014  0.8043  0.8057   
qda       Quadratic Discriminant Analysis    0.5010  0.6321  0.3652  0.4519   
svm                   SVM - Linear Kernel    0.8496  0.0000  0.7764  0.8575   
ridge                    Ridge Classifier    0.8119  0.0000  0.6168  0.7987   

              F1   Kappa     MCC  TT (Sec)  
et        0.8966  0.8177  0.8187     0.818  
lightgbm  0.8980  0.8207  0.8213     0.472  
gbc       0.8934  0.8125  0.8130     2.302  
rf        0.8929  0.8111  0.8123     0.896  
lr        0.8896  0.8060  0.8063     1.010  
lda       0.8675  0.7683  0.7686     0.046  
knn       0.8534  0.7434  0.7438     0.392  
dt        0.8378  0.7163  0.7164     0.050  
nb        0.6000  0.4401  0.4979     0.028  
ada       0.7769  0.6299  0.6483     0.294  
qda       0.4049  0.0790  0.1080     0.034  
svm       0.8445  0.7340  0.7388     0.108  
ridge     0.7867  0.6533  0.6598     0.026

In [ ]:
ebc = ExplainableBoostingClassifier(n_jobs=-1)
ebm = create_model(ebc,fold = 5)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.9049  0.9532  0.9411  0.8887  0.9141  0.8077  0.8093
1       0.8979  0.9563  0.9190  0.8943  0.9064  0.7942  0.7945
2       0.9177  0.9593  0.9282  0.9197  0.9239  0.8344  0.8344
3       0.8821  0.9451  0.8856  0.8939  0.8897  0.7630  0.7630
4       0.9049  0.9541  0.9244  0.9011  0.9126  0.8083  0.8086
Mean    0.9015  0.9536  0.9196  0.8995  0.9094  0.8015  0.8020
SD      0.0116  0.0048  0.0185  0.0108  0.0113  0.0232  0.0233

In [ ]:
df_test_evaluation = []
for model in top5:
  predict_model(model,verbose=0);
  test_performance = pull();
  df_test_evaluation.append(test_performance)

df_test_evaluation = pd.concat(df_test_evaluation)
df_test_evaluation.reset_index(drop=True).sort_values('AUC',ascending=False)

Model  Accuracy     AUC  ...      F1   Kappa     MCC
3         Random Forest Classifier    0.8597  0.9349  ...  0.8590  0.7488  0.7491
2     Gradient Boosting Classifier    0.8664  0.9335  ...  0.8664  0.7635  0.7635
0           Extra Trees Classifier    0.8664  0.9321  ...  0.8654  0.7607  0.7611
1  Light Gradient Boosting Machine    0.8479  0.9287  ...  0.8475  0.7306  0.7311
4              Logistic Regression    0.8529  0.9285  ...  0.8525  0.7392  0.7396

[5 rows x 8 columns]

In [ ]:
from interpret import show

ebm_global = ebm.explain_global(name='EBM')
show(ebm_global)

## Experiment - AD vs MCI

In [ ]:
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['MCI','AD'])

df_train.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)
df_test.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)

exp_clinical = setup(
data = df_train,
test_data=df_test, 
target = 'DIAGNOSIS', 
transformation=True,remove_multicollinearity = False,
session_id=1,experiment_name = 'adni_tabular_ad_mci',silent=True)

Description                Value
0                               session_id                    1
1                                   Target            DIAGNOSIS
2                              Target Type           Multiclass
3                            Label Encoded     0: 0, 1: 1, 2: 2
4                            Original Data           (2949, 24)
5                           Missing Values                False
6                         Numeric Features                   13
7                     Categorical Features                   10
8                         Ordinal Features                False
9                High Cardinality Features                False
10                 High Cardinality Method                 None
11                   Transformed Train Set           (2949, 36)
12                    Transformed Test Set            (751, 36)
13                      Shuffle Train-Test                 True
14                     Stratify Train-Test                False
15                          Fold Generator      StratifiedKFold
16                             Fold Number                   10
17                                CPU Jobs                   -1
18                                 Use GPU                False
19                          Log Experiment                False
20                         Experiment Name  adni_tabular_ad_mci
21                                     USI                 9f85
22                         Imputation Type               simple
23          Iterative Imputation Iteration                 None
24                         Numeric Imputer                 mean
25      Iterative Imputation Numeric Model                 None
26                     Categorical Imputer             constant
27  Iterative Imputation Categorical Model                 None
28           Unknown Categoricals Handling       least_frequent
29                               Normalize                False
30                        Normalize Method                 None
31                          Transformation                 True
32                   Transformation Method          yeo-johnson
33                                     PCA                False
34                              PCA Method                 None
35                          PCA Components                 None
36                     Ignore Low Variance                False
37                     Combine Rare Levels                False
38                    Rare Level Threshold                 None
39                         Numeric Binning                False
40                         Remove Outliers                False
41                      Outliers Threshold                 None
42                Remove Multicollinearity                False
43             Multicollinearity Threshold                 None
44                              Clustering                False
45                    Clustering Iteration                 None
46                     Polynomial Features                False
47                       Polynomial Degree                 None
48                    Trignometry Features                False
49                    Polynomial Threshold                 None
50                          Group Features                False
51                       Feature Selection                False
52                Feature Selection Method              classic
53            Features Selection Threshold                 None
54                     Feature Interaction                False
55                           Feature Ratio                False
56                   Interaction Threshold                 None
57                           Fix Imbalance                False
58                    Fix Imbalance Method                SMOTE

In [ ]:
top5 = compare_models(sort='AUC',n_select = 5,turbo=True,cross_validation = True,fold = 5)

Model  Accuracy     AUC  Recall   Prec.  \
lightgbm  Light Gradient Boosting Machine    0.9067  0.9600  0.8057  0.9049   
et                 Extra Trees Classifier    0.8993  0.9558  0.7584  0.8977   
rf               Random Forest Classifier    0.9047  0.9555  0.7885  0.9032   
gbc          Gradient Boosting Classifier    0.9020  0.9542  0.8044  0.9003   
lr                    Logistic Regression    0.8867  0.9463  0.7779  0.8850   
lda          Linear Discriminant Analysis    0.8718  0.9401  0.7659  0.8712   
knn                K Neighbors Classifier    0.8657  0.9200  0.7008  0.8606   
ada                  Ada Boost Classifier    0.6684  0.8822  0.7742  0.8224   
dt               Decision Tree Classifier    0.8447  0.8274  0.7597  0.8486   
nb                            Naive Bayes    0.3120  0.7358  0.6557  0.7821   
qda       Quadratic Discriminant Analysis    0.7043  0.4996  0.3330  0.4969   
svm                   SVM - Linear Kernel    0.8633  0.0000  0.6488  0.8521   
ridge                    Ridge Classifier    0.8549  0.0000  0.5861  0.8014   

              F1   Kappa     MCC  TT (Sec)  
lightgbm  0.9047  0.7834  0.7850     0.332  
et        0.8945  0.7592  0.7645     0.694  
rf        0.9017  0.7759  0.7789     0.772  
gbc       0.9005  0.7748  0.7758     1.600  
lr        0.8851  0.7402  0.7412     0.248  
lda       0.8712  0.7123  0.7125     0.036  
knn       0.8590  0.6789  0.6835     0.220  
ada       0.6919  0.4527  0.5125     0.230  
dt        0.8461  0.6559  0.6566     0.040  
nb        0.2434  0.1943  0.3514     0.026  
qda       0.5827 -0.0012 -0.0065     0.030  
svm       0.8470  0.6731  0.6815     0.084  
ridge     0.8268  0.6403  0.6513     0.022

In [ ]:
ebc = ExplainableBoostingClassifier(n_jobs=1)
ebm = create_model(ebc,fold = 5)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.9413  0.9846  0.9617  0.9582  0.9599  0.8499  0.8499
1       0.9199  0.9698  0.9544  0.9373  0.9458  0.7927  0.7932
2       0.9359  0.9763  0.9653  0.9480  0.9566  0.8342  0.8347
3       0.9279  0.9646  0.9580  0.9442  0.9511  0.8141  0.8144
4       0.9119  0.9677  0.9453  0.9350  0.9401  0.7735  0.7736
Mean    0.9274  0.9726  0.9569  0.9445  0.9507  0.8129  0.8132
SD      0.0106  0.0071  0.0069  0.0083  0.0072  0.0275  0.0275

In [ ]:
df_test_evaluation = []
for model in top5:
  predict_model(model,verbose=0);
  test_performance = pull();
  df_test_evaluation.append(test_performance)

df_test_evaluation = pd.concat(df_test_evaluation)
df_test_evaluation.reset_index(drop=True).sort_values('AUC',ascending=False)

Model  Accuracy     AUC  ...      F1   Kappa     MCC
3     Gradient Boosting Classifier    0.8815  0.9483  ...  0.8762  0.6883  0.6898
4              Logistic Regression    0.8855  0.9466  ...  0.8826  0.7035  0.7040
0  Light Gradient Boosting Machine    0.8881  0.9462  ...  0.8831  0.7095  0.7105
2         Random Forest Classifier    0.8842  0.9415  ...  0.8788  0.6940  0.6958
1           Extra Trees Classifier    0.8775  0.9402  ...  0.8680  0.6706  0.6741

[5 rows x 8 columns]

In [ ]:
from interpret import show

ebm_global = ebm.explain_global(name='EBM')
show(ebm_global)

## Experiment - CN vs AD

In [ ]:
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['CN','AD'])

df_train.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)
df_test.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)

exp_clinical = setup(
data = df_train,
test_data=df_test,
target = 'DIAGNOSIS',
transformation=True,
remove_multicollinearity = False,
session_id=1,
experiment_name = 'adni_tabular_cn_ad',silent=True)

Description               Value
0                               session_id                   1
1                                   Target           DIAGNOSIS
2                              Target Type          Multiclass
3                            Label Encoded    0: 0, 1: 1, 2: 2
4                            Original Data          (2342, 24)
5                           Missing Values               False
6                         Numeric Features                  13
7                     Categorical Features                  10
8                         Ordinal Features               False
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set          (2342, 36)
12                    Transformed Test Set           (579, 36)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                  10
17                                CPU Jobs                  -1
18                                 Use GPU               False
19                          Log Experiment               False
20                         Experiment Name  adni_tabular_cn_ad
21                                     USI                3a41
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer                mean
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer            constant
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling      least_frequent
29                               Normalize               False
30                        Normalize Method                None
31                          Transformation                True
32                   Transformation Method         yeo-johnson
33                                     PCA               False
34                              PCA Method                None
35                          PCA Components                None
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers               False
41                      Outliers Threshold                None
42                Remove Multicollinearity               False
43             Multicollinearity Threshold                None
44                              Clustering               False
45                    Clustering Iteration                None
46                     Polynomial Features               False
47                       Polynomial Degree                None
48                    Trignometry Features               False
49                    Polynomial Threshold                None
50                          Group Features               False
51                       Feature Selection               False
52                Feature Selection Method             classic
53            Features Selection Threshold                None
54                     Feature Interaction               False
55                           Feature Ratio               False
56                   Interaction Threshold                None
57                           Fix Imbalance               False
58                    Fix Imbalance Method               SMOTE

In [ ]:
# selected_models = ['lr','rbfsvm','rf']
top5 = compare_models(sort='AUC',n_select = 5,turbo=True,cross_validation = True,fold = 5)

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.9398  0.9851  0.8316  0.9353   
rf               Random Forest Classifier    0.9278  0.9833  0.8006  0.9206   
gbc          Gradient Boosting Classifier    0.9313  0.9826  0.8303  0.9282   
lightgbm  Light Gradient Boosting Machine    0.9321  0.9821  0.8398  0.9296   
lr                    Logistic Regression    0.9283  0.9794  0.8274  0.9243   
lda          Linear Discriminant Analysis    0.9184  0.9778  0.8473  0.9249   
knn                K Neighbors Classifier    0.9189  0.9632  0.7781  0.9080   
nb                            Naive Bayes    0.2400  0.9567  0.5235  0.8821   
ada                  Ada Boost Classifier    0.8920  0.9370  0.7873  0.9019   
dt               Decision Tree Classifier    0.9116  0.9036  0.8083  0.9115   
qda       Quadratic Discriminant Analysis    0.6592  0.4982  0.3296  0.5661   
svm                   SVM - Linear Kernel    0.9236  0.0000  0.8081  0.9171   
ridge                    Ridge Classifier    0.9048  0.0000  0.6959  0.8863   

              F1   Kappa     MCC  TT (Sec)  
et        0.9355  0.8480  0.8504     0.662  
rf        0.9220  0.8163  0.8196     0.716  
gbc       0.9289  0.8292  0.8303     1.340  
lightgbm  0.9303  0.8323  0.8331     0.302  
lr        0.9254  0.8236  0.8245     0.186  
lda       0.9208  0.8081  0.8095     0.034  
knn       0.9106  0.7935  0.7970     0.154  
nb        0.2395  0.1126  0.2799     0.028  
ada       0.8954  0.7431  0.7453     0.208  
dt        0.9113  0.7856  0.7859     0.030  
qda       0.5838 -0.0019 -0.0002     0.030  
svm       0.9191  0.8094  0.8110     0.076  
ridge     0.8759  0.7513  0.7642     0.022

In [ ]:
ebc = ExplainableBoostingClassifier(n_jobs=-1)
ebm = create_model(ebc,fold = 5)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.9168  0.9705  0.7877  0.9088  0.9116  0.7902  0.7924
1       0.9382  0.9893  0.8587  0.9361  0.9370  0.8495  0.8497
2       0.9145  0.9722  0.7855  0.9096  0.9112  0.7835  0.7854
3       0.9444  0.9844  0.8391  0.9405  0.9403  0.8607  0.8625
4       0.9231  0.9767  0.7804  0.9141  0.9151  0.8001  0.8058
Mean    0.9274  0.9786  0.8103  0.9218  0.9230  0.8168  0.8191
SD      0.0119  0.0072  0.0322  0.0136  0.0128  0.0319  0.0311

In [ ]:
top5.append(ebm)
df_test_evaluation = []
for model in top5:
  predict_model(model,verbose=0);
  test_performance = pull();
  df_test_evaluation.append(test_performance)

df_test_evaluation = pd.concat(df_test_evaluation)
df_test_evaluation.reset_index(drop=True).sort_values('AUC',ascending=False)

Model  Accuracy     AUC  ...      F1   Kappa     MCC
0           Extra Trees Classifier    0.9447  0.9924  ...  0.9421  0.8485  0.8493
4              Logistic Regression    0.9361  0.9920  ...  0.9375  0.8315  0.8316
5    ExplainableBoostingClassifier    0.9344  0.9908  ...  0.9338  0.8221  0.8225
1         Random Forest Classifier    0.9326  0.9905  ...  0.9303  0.8155  0.8163
2     Gradient Boosting Classifier    0.9257  0.9895  ...  0.9238  0.7984  0.7988
3  Light Gradient Boosting Machine    0.9240  0.9890  ...  0.9270  0.7977  0.7982

[6 rows x 8 columns]

In [ ]:
from interpret import show

ebm_global = ebm.explain_global(name='EBM')
show(ebm_global)

## Experiment - AD vs MCI vs CN

In [ ]:
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=['MCI','AD','CN'])

df_train.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)
df_test.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)

exp_clinical = setup(
data = df_train,
test_data=df_test, 
target = 'DIAGNOSIS', 
transformation=True,remove_multicollinearity = False,
session_id=1,experiment_name = 'adni_tabular_ad_mci_cn',silent=True)

Description                   Value
0                               session_id                       1
1                                   Target               DIAGNOSIS
2                              Target Type              Multiclass
3                            Label Encoded        0: 0, 1: 1, 2: 2
4                            Original Data              (4993, 24)
5                           Missing Values                   False
6                         Numeric Features                      13
7                     Categorical Features                      10
8                         Ordinal Features                   False
9                High Cardinality Features                   False
10                 High Cardinality Method                    None
11                   Transformed Train Set              (4993, 37)
12                    Transformed Test Set              (1217, 37)
13                      Shuffle Train-Test                    True
14                     Stratify Train-Test                   False
15                          Fold Generator         StratifiedKFold
16                             Fold Number                      10
17                                CPU Jobs                      -1
18                                 Use GPU                   False
19                          Log Experiment                   False
20                         Experiment Name  adni_tabular_ad_mci_cn
21                                     USI                    fa96
22                         Imputation Type                  simple
23          Iterative Imputation Iteration                    None
24                         Numeric Imputer                    mean
25      Iterative Imputation Numeric Model                    None
26                     Categorical Imputer                constant
27  Iterative Imputation Categorical Model                    None
28           Unknown Categoricals Handling          least_frequent
29                               Normalize                   False
30                        Normalize Method                    None
31                          Transformation                    True
32                   Transformation Method             yeo-johnson
33                                     PCA                   False
34                              PCA Method                    None
35                          PCA Components                    None
36                     Ignore Low Variance                   False
37                     Combine Rare Levels                   False
38                    Rare Level Threshold                    None
39                         Numeric Binning                   False
40                         Remove Outliers                   False
41                      Outliers Threshold                    None
42                Remove Multicollinearity                   False
43             Multicollinearity Threshold                    None
44                              Clustering                   False
45                    Clustering Iteration                    None
46                     Polynomial Features                   False
47                       Polynomial Degree                    None
48                    Trignometry Features                   False
49                    Polynomial Threshold                    None
50                          Group Features                   False
51                       Feature Selection                   False
52                Feature Selection Method                 classic
53            Features Selection Threshold                    None
54                     Feature Interaction                   False
55                           Feature Ratio                   False
56                   Interaction Threshold                    None
57                           Fix Imbalance                   False
58                    Fix Imbalance Method                   SMOTE

In [ ]:
top5 = compare_models(sort='AUC',n_select = 5,turbo=True,cross_validation = True,fold = 5)

Model  Accuracy     AUC  Recall   Prec.  \
lightgbm  Light Gradient Boosting Machine    0.8842  0.9623  0.8707  0.8850   
et                 Extra Trees Classifier    0.8840  0.9617  0.8694  0.8853   
rf               Random Forest Classifier    0.8818  0.9575  0.8678  0.8839   
gbc          Gradient Boosting Classifier    0.8816  0.9575  0.8718  0.8829   
lr                    Logistic Regression    0.8744  0.9503  0.8656  0.8749   
lda          Linear Discriminant Analysis    0.8574  0.9441  0.8632  0.8600   
knn                K Neighbors Classifier    0.8436  0.9324  0.8294  0.8435   
nb                            Naive Bayes    0.6788  0.8655  0.7563  0.7502   
dt               Decision Tree Classifier    0.8215  0.8494  0.8149  0.8220   
ada                  Ada Boost Classifier    0.7428  0.6869  0.7988  0.7672   
qda       Quadratic Discriminant Analysis    0.4370  0.6116  0.3417  0.3820   
svm                   SVM - Linear Kernel    0.8442  0.0000  0.8233  0.8488   
ridge                    Ridge Classifier    0.7949  0.0000  0.7545  0.7925   

              F1   Kappa     MCC  TT (Sec)  
lightgbm  0.8842  0.8088  0.8092     0.402  
et        0.8841  0.8083  0.8089     0.860  
rf        0.8819  0.8044  0.8056     0.966  
gbc       0.8817  0.8046  0.8052     2.574  
lr        0.8744  0.7934  0.7936     0.404  
lda       0.8577  0.7686  0.7694     0.048  
knn       0.8433  0.7427  0.7430     0.542  
nb        0.6472  0.5129  0.5585     0.032  
dt        0.8216  0.7066  0.7068     0.058  
ada       0.7333  0.5961  0.6152     0.330  
qda       0.3043  0.0147  0.0345     0.042  
svm       0.8425  0.7428  0.7454     0.126  
ridge     0.7918  0.6602  0.6616     0.028

In [ ]:
ebc = ExplainableBoostingClassifier(n_jobs=1)
ebm = create_model(ebc,fold = 5)

In [ ]:
df_test_evaluation = []
for model in top5:
  predict_model(model,verbose=0);
  test_performance = pull();
  df_test_evaluation.append(test_performance)

df_test_evaluation = pd.concat(df_test_evaluation)
df_test_evaluation.reset_index(drop=True).sort_values('AUC',ascending=False)

Model  Accuracy     AUC  ...      F1   Kappa     MCC
3     Gradient Boosting Classifier    0.8833  0.9611  ...  0.8830  0.8087  0.8089
2         Random Forest Classifier    0.8841  0.9586  ...  0.8838  0.8092  0.8096
0  Light Gradient Boosting Machine    0.8702  0.9577  ...  0.8697  0.7876  0.7882
4              Logistic Regression    0.8710  0.9552  ...  0.8706  0.7895  0.7899
1           Extra Trees Classifier    0.8759  0.9524  ...  0.8753  0.7955  0.7962

[5 rows x 8 columns]

In [ ]:
from interpret import show

ebm_global = ebm.explain_global(name='EBM')
show(ebm_global)

## Experiment New Code - AD vs CN

In [ ]:
import numpy as np
import pandas as pd

def train_test_split_by_subject(df,test_size = 0.3,labels = ['AD','CN'],label_column = 'MACRO_GROUP',random_seed=42):
    
    '''
    Splits the dataset on train and test, at patient level (to avoid data leakage).
    This process executes a stratified random split, that is, it maintains the proportion of each class in the sets.
    
    Parameters
    ----------

    df: Reference dataframe containing information about patients.
    
    test_size: test dataset size. Value must be between bigger than 0 and less than 1.

    labels: Label of the classes.
    
    label_column: Name of the column in the dataframe that contains the classes.
    
    Returns
    ----------
    Tuple with train and test reference datasets: df_train, df_test
    
    '''

    train = []
    test = []
    df_classes = df[df[label_column].isin(labels)]

    # split by subject id
    subjects = df_classes['SUBJECT'].unique()
    
    rng = np.random.default_rng(random_seed)

    for label in labels:
        subjects = df_classes.query(label_column +" == @label")['SUBJECT'].unique()
        rng.shuffle(subjects)

        test_subjects_quantity = int(np.ceil(test_size * subjects.shape[0]))
        test_subjects = subjects[:test_subjects_quantity]
        train_subjects = subjects[test_subjects_quantity:]
        
        df_train_cl = df_classes.query("SUBJECT in @train_subjects")
        df_test_cl = df_classes.query("SUBJECT in @test_subjects")
        train.append(df_train_cl)
        test.append(df_test_cl)

    df_train = pd.concat(train).sample(frac=1).reset_index(drop=True)
    df_test = pd.concat(test).sample(frac=1).reset_index(drop=True)

    return df_train,df_test


In [ ]:
import numpy as np
import pandas as pd

def stratified_fold_split_by_subject(df, n_splits=10, labels = ['AD','CN'], label_column = 'MACRO_GROUP', random_seed=42, return_indices=False):

    '''
    Provides train/test fold indices to split data at patient level, in order to avoid data leakage.
    
    This process executes a stratified random split, that is, it maintains the proportion of each class in the sets.
    
    Parameters
    ----------

    df: Reference dataframe containing information about patients.
    
    n_splits: number to determine the amount of fold splits in data.

    labels: Label of the classes.
    
    label_column: Name of the column in the dataframe that contains the classes.
    
    return_indices: Flag to return the train/test indices. If False, it returns the entire reference dataframes.

    Returns
    ----------
    Tuple with train and test reference datasets: df_train, df_test


    Example
    ----------

    y = df_adni_merge['DIAGNOSIS']
    X = df_adni_merge.drop(['DIAGNOSIS'],axis=1)

    for train_index, test_index in stratified_fold_split_by_subject(df, n_splits=10,labels = ['AD','CN'],label_column = 'DIAGNOSIS_BASELINE',return_indices=True):
        X_train = df_adni_merge.query(index in @)

        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        ...
        ...
        ...

    ---------

    y = df_adni_merge['DIAGNOSIS']
    X = df_adni_merge.drop(['DIAGNOSIS'],axis=1)

    results = sklearn.model_selection.cross_validate(
                                ExplainableBoostingClassifier(**ebm_params),
                                X,y,
                                cv=stratified_fold_split_by_subject(df, n_splits=10,labels = ['AD','CN'],label_column = 'DIAGNOSIS_BASELINE',return_indices=True),
                                scoring=my_auc,n_jobs=-1)
    '''

    train = []
    test = []
    df_classes = df[df[label_column].isin(labels)].copy()
    df_classes['FOLD'] = 0

    # split by subject id
    subjects = df_classes['SUBJECT'].unique()
    
    rng = np.random.default_rng(random_seed)

    for label in labels:
        subjects = df_classes.query(label_column +" == @label")['SUBJECT'].unique()
        rng.shuffle(subjects)

        n_subjects = subjects.shape[0]
        fold_size = int(np.ceil(n_subjects / n_splits))

        subjects_by_fold = np.array_split(subjects,n_splits)
        for split in range(n_splits):
            fold_subjects = subjects_by_fold[split]
            df_classes.loc[df_classes['SUBJECT'].isin(fold_subjects),'FOLD'] = split

    if return_indices:
        for split in range(n_splits):
            train_index = df_classes.query("FOLD != @split").index
            test_index = df_classes.query("FOLD == @split").index
            yield train_index,test_index
    else:
        return df_classes


class StratifiedSubjectKFold:
    def __init__(self,df,classes = [0,1] , n_splits=3):
        self.n_splits = n_splits
        self.df = df.copy()
        self.classes = classes

    def split(self, X, y, groups=None):

        return stratified_fold_split_by_subject(self.df, n_splits=self.n_splits,labels = self.classes,label_column = 'DIAGNOSIS_BASELINE',return_indices=True)
        
    def get_n_splits(self, X, y, groups=None):
        return self.n_splits

In [ ]:
df_adni_merge = pd.read_csv("./data/tabular/COGNITIVE_DATA_PROCESSED.csv")
organized_cols = ['SUBJECT','DIAGNOSIS','DIAGNOSIS_BASELINE','AGE', 'MALE', 'YEARS_EDUCATION', 'HISPANIC',
'RACE_WHITE', 'RACE_BLACK', 'RACE_ASIAN',
'MARRIED','WIDOWED','DIVORCED','NEVER_MARRIED', 'CDRSB', 'ADAS11', 'ADAS13', 'ADASQ4', 'MMSE',
'RAVLT_immediate', 'RAVLT_learning', 'RAVLT_forgetting',
'RAVLT_perc_forgetting', 'TRABSCOR', 'FAQ',
'MOCA']

df_adni_merge = df_adni_merge[organized_cols]
df_adni_merge.shape

(10720, 26)

In [ ]:
df_adni_merge = df_adni_merge.dropna()
df_adni_merge.reset_index(drop=True,inplace=True)
df_adni_merge.shape

(6210, 26)

In [ ]:
labels = ['CN','AD']
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=labels)

# df_train.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)
# df_test.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1,inplace=True)

exp_clinical = setup(
data = df_train.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1),
test_data=df_test.drop(["SUBJECT",'DIAGNOSIS_BASELINE'],axis=1),
fold_strategy = StratifiedSubjectKFold(df_train,classes=labels,n_splits=5),
target = 'DIAGNOSIS',
transformation=True,
remove_multicollinearity = False,
session_id=1,
experiment_name = 'adni_tabular_cn_ad',silent=True)

Description                   Value
0                               session_id                       1
1                                   Target               DIAGNOSIS
2                              Target Type              Multiclass
3                            Label Encoded        0: 0, 1: 1, 2: 2
4                            Original Data              (2323, 24)
5                           Missing Values                   False
6                         Numeric Features                      13
7                     Categorical Features                      10
8                         Ordinal Features                   False
9                High Cardinality Features                   False
10                 High Cardinality Method                    None
11                   Transformed Train Set              (2323, 36)
12                    Transformed Test Set               (598, 36)
13                      Shuffle Train-Test                    True
14                     Stratify Train-Test                   False
15                          Fold Generator  StratifiedSubjectKFold
16                             Fold Number                      10
17                                CPU Jobs                      -1
18                                 Use GPU                   False
19                          Log Experiment                   False
20                         Experiment Name      adni_tabular_cn_ad
21                                     USI                    cf16
22                         Imputation Type                  simple
23          Iterative Imputation Iteration                    None
24                         Numeric Imputer                    mean
25      Iterative Imputation Numeric Model                    None
26                     Categorical Imputer                constant
27  Iterative Imputation Categorical Model                    None
28           Unknown Categoricals Handling          least_frequent
29                               Normalize                   False
30                        Normalize Method                    None
31                          Transformation                    True
32                   Transformation Method             yeo-johnson
33                                     PCA                   False
34                              PCA Method                    None
35                          PCA Components                    None
36                     Ignore Low Variance                   False
37                     Combine Rare Levels                   False
38                    Rare Level Threshold                    None
39                         Numeric Binning                   False
40                         Remove Outliers                   False
41                      Outliers Threshold                    None
42                Remove Multicollinearity                   False
43             Multicollinearity Threshold                    None
44                              Clustering                   False
45                    Clustering Iteration                    None
46                     Polynomial Features                   False
47                       Polynomial Degree                    None
48                    Trignometry Features                   False
49                    Polynomial Threshold                    None
50                          Group Features                   False
51                       Feature Selection                   False
52                Feature Selection Method                 classic
53            Features Selection Threshold                    None
54                     Feature Interaction                   False
55                           Feature Ratio                   False
56                   Interaction Threshold                    None
57                           Fix Imbalance                   False
58                    Fix Imbalance Method                   SMOTE

In [ ]:
# selected_models = ['lr','rf']
top5 = compare_models(sort='AUC',n_select = 5,turbo=True,cross_validation = True)

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.9265  0.9808  0.7864  0.9175   
lda          Linear Discriminant Analysis    0.9189  0.9804  0.8602  0.9277   
lr                    Logistic Regression    0.9283  0.9799  0.8139  0.9219   
gbc          Gradient Boosting Classifier    0.9244  0.9785  0.8000  0.9171   
lightgbm  Light Gradient Boosting Machine    0.9188  0.9763  0.7840  0.9096   
rf               Random Forest Classifier    0.9209  0.9756  0.7740  0.9103   
nb                            Naive Bayes    0.4690  0.9468  0.6584  0.9038   
ada                  Ada Boost Classifier    0.9028  0.9422  0.7696  0.8988   
knn                K Neighbors Classifier    0.9205  0.9416  0.7757  0.9101   
dt               Decision Tree Classifier    0.8862  0.8751  0.7556  0.8885   
qda       Quadratic Discriminant Analysis    0.6885  0.4923  0.3276  0.5574   
svm                   SVM - Linear Kernel    0.9136  0.0000  0.7277  0.8982   
ridge                    Ridge Classifier    0.9037  0.0000  0.6879  0.8729   

              F1   Kappa     MCC  TT (Sec)  
et        0.9185  0.8087  0.8128     0.594  
lda       0.9221  0.8074  0.8096     0.038  
lr        0.9239  0.8166  0.8180     0.182  
gbc       0.9191  0.8064  0.8085     1.134  
lightgbm  0.9123  0.7917  0.7941     0.362  
rf        0.9125  0.7937  0.7980     0.664  
nb        0.5351  0.2675  0.4043     0.030  
ada       0.8996  0.7560  0.7575     0.186  
knn       0.9111  0.7939  0.7978     0.156  
dt        0.8870  0.7219  0.7225     0.034  
qda       0.6094 -0.0106 -0.0114     0.036  
svm       0.8953  0.7674  0.7789     0.084  
ridge     0.8721  0.7443  0.7575     0.034

In [ ]:
# import optuna
from sklearn.model_selection import cross_validate
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import StratifiedKFold

my_auc = make_scorer(roc_auc_score, greater_is_better=True, needs_proba=True)
count_iteration = 1

labels = ['CN','AD']
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS_BASELINE',labels=labels)
df_train = df_train.reset_index(drop=True)
# X_train = df_train.drop(['DIAGNOSIS','SUBJECT','DIAGNOSIS_BASELINE'],axis=1)
# y_train = df_train['DIAGNOSIS']

results = cross_validate(ExplainableBoostingClassifier(),df_train.drop(['DIAGNOSIS','SUBJECT','DIAGNOSIS_BASELINE'],axis=1),df_train['DIAGNOSIS'],cv=StratifiedSubjectKFold(df_train,classes=labels,n_splits=5),scoring=my_auc,n_jobs=-1)
print("AUC=",results['test_score'].mean(), "+/-", results['test_score'].std())

ValueError: ignored

In [ ]:
X = df_train.drop(['DIAGNOSIS'],axis=1)
y = df_train['DIAGNOSIS']
sfold = StratifiedSubjectKFold(df_train,classes=labels,n_splits=3)
# TODO: Está com um bug aqui na seleção de indices, parece q está selecionando multiplas classes
for fold in sfold.split(X,y):
  print(fold[0].shape,fold[1].shape)
  print('----------------------')

  X_train = X.values[fold[0]]
  y_train = y.values[fold[0]]

(1542,) (781,)
----------------------
(1522,) (801,)
----------------------
(1582,) (741,)
----------------------


In [ ]:
pd.Series(y_train).unique()

array([0, 1, 2])

# Experiment with TADPOLE Data - AD vs MCI vs CN

In [ ]:
df_tadpole = pd.read_csv("./data/tadpole/TADPOLE_D1_D2.csv")

baseline_cols = [x for x in df_tadpole.columns if '_bl' in x] + ['update_stamp']
df_tadpole.drop(baseline_cols,axis=1,inplace=True)

In [ ]:
df_tadpole['DX'].value_counts()

MCI                3932
NL                 2668
Dementia           1732
MCI to Dementia     372
NL to MCI           108
MCI to NL            77
Dementia to MCI      12
NL to Dementia        3
Name: DX, dtype: int64

In [ ]:
df_adni_merge.loc[df_adni_merge['DX'] == 'Dementia','DX'] = 'AD'

neuropsychological_cols = ['CDRSB','ADAS11', 'ADAS13', 'ADASQ4', 'MMSE', 'RAVLT_immediate',
'RAVLT_learning', 'RAVLT_forgetting', 'RAVLT_perc_forgetting',
'LDELTOTAL', 'DIGITSCOR', 'TRABSCOR', 'FAQ', 'MOCA', 'EcogPtMem',
'EcogPtLang', 'EcogPtVisspat', 'EcogPtPlan', 'EcogPtOrgan',
'EcogPtDivatt', 'EcogPtTotal', 'EcogSPMem', 'EcogSPLang',
'EcogSPVisspat', 'EcogSPPlan', 'EcogSPOrgan', 'EcogSPDivatt','EcogSPTotal']

demographics_cols = ['AGE','PTGENDER', 'PTEDUCAT','PTETHCAT', 'PTRACCAT', 'PTMARRY']

id_cols = ['RID', 'PTID', 'VISCODE', 'SITE', 'COLPROT', 'ORIGPROT', 'EXAMDATE','IMAGEUID','DX']
df_adni_merge = df_adni_merge[id_cols + demographics_cols + neuropsychological_cols]

df_adni_merge = df_adni_merge[~df_adni_merge['DX'].isnull()]

df_adni_merge.rename(inplace=True,
    columns={
    'PTRACCAT':'RACE',
    'PTMARRY':'MARRIED',
    'PTEDUCAT':'YEARS_EDUCATION',
    'PTGENDER':'MALE',
    'PTETHCAT':'HISPANIC',
    'DX':'DIAGNOSIS',
    'PTID':'SUBJECT'
})

df_adni_merge.loc[df_adni_merge['RACE'].isin(["More than one",'Unkown','Unknown','Hawaiian/Other PI','Am Indian/Alaskan']),'RACE'] = 'Other races'
df_adni_merge['RACE_WHITE'] = (df_adni_merge['RACE'] == 'White').astype(int)
df_adni_merge['RACE_BLACK'] = (df_adni_merge['RACE'] == 'Black').astype(int)
df_adni_merge['RACE_ASIAN'] = (df_adni_merge['RACE'] == 'Asian').astype(int)
# df_adni_merge['RACE_OTHER'] = df_adni_merge['RACE'] == 'Other races'

df_adni_merge.loc[df_adni_merge['HISPANIC'] == 'Not Hisp/Latino','HISPANIC'] = 0
df_adni_merge.loc[df_adni_merge['HISPANIC'] == 'Unknown','HISPANIC'] = 0
df_adni_merge.loc[df_adni_merge['HISPANIC'] == 'Hisp/Latino','HISPANIC'] = 1

df_adni_merge['IMAGEUID'] = df_adni_merge['IMAGEUID'].fillna(999999)
df_adni_merge['IMAGEUID'] = df_adni_merge['IMAGEUID'].astype(int)

df_adni_merge.loc[df_adni_merge['DIAGNOSIS'] == 'AD','DIAGNOSIS'] = 1
df_adni_merge.loc[df_adni_merge['DIAGNOSIS'] == 'CN','DIAGNOSIS'] = 0
df_adni_merge.loc[df_adni_merge['DIAGNOSIS'] == 'MCI','DIAGNOSIS'] = 2

df_adni_merge.loc[df_adni_merge['MALE'] == 'Male','MALE'] = 1
df_adni_merge.loc[df_adni_merge['MALE'] == 'Female','MALE'] = 0

df_adni_merge['WIDOWED'] = (df_adni_merge['MARRIED'] == 'Widowed').astype(int)
df_adni_merge['DIVORCED'] = (df_adni_merge['MARRIED'] == 'Divorced').astype(int)
df_adni_merge['NEVER_MARRIED'] = (df_adni_merge['MARRIED'] == 'Never married').astype(int)

df_adni_merge['MARRIED'] = (df_adni_merge['MARRIED'] == 'Married').astype(int)

In [ ]:
df_tadpole = pd.read_csv("./data/tabular/TADPOLE_D1_D2.csv")

organized_cols = ['SUBJECT','DIAGNOSIS','AGE', 'MALE', 'YEARS_EDUCATION', 'HISPANIC',
'RACE_WHITE', 'RACE_BLACK', 'RACE_ASIAN',
'MARRIED','WIDOWED','DIVORCED','NEVER_MARRIED', 'CDRSB', 'ADAS11', 'ADAS13', 'ADASQ4', 'MMSE',
'RAVLT_immediate', 'RAVLT_learning', 'RAVLT_forgetting',
'RAVLT_perc_forgetting', 'LDELTOTAL', 'DIGITSCOR', 'TRABSCOR', 'FAQ',
'MOCA', 'EcogPtMem', 'EcogPtLang', 'EcogPtVisspat', 'EcogPtPlan',
'EcogPtOrgan', 'EcogPtDivatt', 'EcogPtTotal', 'EcogSPMem', 'EcogSPLang',
'EcogSPVisspat', 'EcogSPPlan', 'EcogSPOrgan', 'EcogSPDivatt',
'EcogSPTotal']

df_adni_merge = df_adni_merge[organized_cols]

In [ ]:
df_train, df_test = train_test_split_by_subject(df_adni_merge,test_size=0.2,label_column='DIAGNOSIS',labels=[2,1,0])

df_train.drop("SUBJECT",axis=1,inplace=True)
df_test.drop("SUBJECT",axis=1,inplace=True)

exp_clinical = setup(
data = df_train,
test_data=df_test, 
target = 'DIAGNOSIS', 
transformation=True,remove_multicollinearity = False,
session_id=1,experiment_name = 'adni_clinal_data_ad_mci_cn',silent=True)

Description                       Value
0                               session_id                           1
1                                   Target                   DIAGNOSIS
2                              Target Type                  Multiclass
3                            Label Encoded            0: 0, 1: 1, 2: 2
4                            Original Data                  (6434, 24)
5                           Missing Values                       False
6                         Numeric Features                          13
7                     Categorical Features                          10
8                         Ordinal Features                       False
9                High Cardinality Features                       False
10                 High Cardinality Method                        None
11                   Transformed Train Set                  (6434, 36)
12                    Transformed Test Set                  (1686, 36)
13                      Shuffle Train-Test                        True
14                     Stratify Train-Test                       False
15                          Fold Generator             StratifiedKFold
16                             Fold Number                          10
17                                CPU Jobs                          -1
18                                 Use GPU                       False
19                          Log Experiment                       False
20                         Experiment Name  adni_clinal_data_ad_mci_cn
21                                     USI                        ea94
22                         Imputation Type                      simple
23          Iterative Imputation Iteration                        None
24                         Numeric Imputer                        mean
25      Iterative Imputation Numeric Model                        None
26                     Categorical Imputer                    constant
27  Iterative Imputation Categorical Model                        None
28           Unknown Categoricals Handling              least_frequent
29                               Normalize                       False
30                        Normalize Method                        None
31                          Transformation                        True
32                   Transformation Method                 yeo-johnson
33                                     PCA                       False
34                              PCA Method                        None
35                          PCA Components                        None
36                     Ignore Low Variance                       False
37                     Combine Rare Levels                       False
38                    Rare Level Threshold                        None
39                         Numeric Binning                       False
40                         Remove Outliers                       False
41                      Outliers Threshold                        None
42                Remove Multicollinearity                       False
43             Multicollinearity Threshold                        None
44                              Clustering                       False
45                    Clustering Iteration                        None
46                     Polynomial Features                       False
47                       Polynomial Degree                        None
48                    Trignometry Features                       False
49                    Polynomial Threshold                        None
50                          Group Features                       False
51                       Feature Selection                       False
52                Feature Selection Method                     classic
53            Features Selection Threshold                        None
54                     Feature Interaction                       False
55                           Feature Ratio             

In [ ]:
top5 = compare_models(sort='AUC',n_select = 5,turbo=False,cross_validation = True,fold = 5)

Model  Accuracy     AUC  Recall   Prec.  \
et                 Extra Trees Classifier    0.9259  0.9835  0.9192  0.9266   
rf               Random Forest Classifier    0.9221  0.9763  0.9151  0.9231   
lightgbm  Light Gradient Boosting Machine    0.9232  0.9745  0.9190  0.9236   
mlp                        MLP Classifier    0.8998  0.9640  0.9014  0.9001   
gbc          Gradient Boosting Classifier    0.8831  0.9586  0.8747  0.8845   
gpc           Gaussian Process Classifier    0.8948  0.9541  0.8869  0.8950   
rbfsvm                SVM - Radial Kernel    0.8657  0.9481  0.8525  0.8682   
lr                    Logistic Regression    0.8662  0.9452  0.8601  0.8667   
lda          Linear Discriminant Analysis    0.8447  0.9388  0.8525  0.8466   
knn                K Neighbors Classifier    0.8376  0.9352  0.8337  0.8379   
dt               Decision Tree Classifier    0.8743  0.8941  0.8748  0.8746   
nb                            Naive Bayes    0.5681  0.8773  0.6878  0.6825   
ada                  Ada Boost Classifier    0.7578  0.7784  0.8033  0.7860   
qda       Quadratic Discriminant Analysis    0.3924  0.5295  0.3369  0.4403   
svm                   SVM - Linear Kernel    0.8289  0.0000  0.8067  0.8327   
ridge                    Ridge Classifier    0.7857  0.0000  0.7592  0.7841   

              F1   Kappa     MCC  TT (Sec)  
et        0.9259  0.8788  0.8793     0.918  
rf        0.9222  0.8726  0.8732     1.020  
lightgbm  0.9232  0.8747  0.8749     0.530  
mlp       0.8998  0.8371  0.8373    13.618  
gbc       0.8831  0.8084  0.8092     2.920  
gpc       0.8947  0.8283  0.8285   136.094  
rbfsvm    0.8658  0.7795  0.7809     3.900  
lr        0.8662  0.7818  0.7820     1.124  
lda       0.8448  0.7503  0.7511     0.060  
knn       0.8374  0.7368  0.7372     0.642  
dt        0.8742  0.7954  0.7956     0.066  
nb        0.4656  0.3770  0.4644     0.030  
ada       0.7494  0.6240  0.6450     0.350  
qda       0.2464  0.0068  0.0375     0.042  
svm       0.8267  0.7191  0.7216     0.122  
ridge     0.7834  0.6496  0.6507     0.028

In [ ]:
ebc = ExplainableBoostingClassifier(n_jobs=1)
ebm = create_model(ebc,fold = 5)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0       0.8741  0.9542  0.8694  0.8752  0.8742  0.7939  0.7945
1       0.8772  0.9526  0.8591  0.8801  0.8771  0.7975  0.7993
2       0.8834  0.9569  0.8722  0.8842  0.8834  0.8091  0.8095
3       0.8632  0.9429  0.8550  0.8648  0.8634  0.7764  0.7772
4       0.8810  0.9488  0.8708  0.8820  0.8810  0.8048  0.8053
Mean    0.8758  0.9511  0.8653  0.8773  0.8758  0.7963  0.7972
SD      0.0070  0.0049  0.0069  0.0069  0.0070  0.0113  0.0112

In [ ]:
df_test_evaluation = []
for model in top5:
  predict_model(model,verbose=0);
  test_performance = pull();
  df_test_evaluation.append(test_performance)

df_test_evaluation = pd.concat(df_test_evaluation)
df_test_evaluation.reset_index(drop=True).sort_values('AUC',ascending=False)

Model  Accuracy     AUC  ...      F1   Kappa     MCC
0           Extra Trees Classifier    0.9247  0.9845  ...  0.9247  0.8758  0.8760
1         Random Forest Classifier    0.9276  0.9811  ...  0.9277  0.8807  0.8810
2  Light Gradient Boosting Machine    0.9241  0.9769  ...  0.9241  0.8749  0.8750
4     Gradient Boosting Classifier    0.8796  0.9615  ...  0.8797  0.8009  0.8016
3                   MLP Classifier    0.8891  0.9590  ...  0.8892  0.8168  0.8173

[5 rows x 8 columns]

In [ ]:
from interpret import show

ebm_global = ebm.explain_global(name='EBM')
show(ebm_global)